In [ ]:
### Autodock preparation ### from: https://www.chem.uwec.edu/chem491_w01/Chem491-Molecules%20and%20Medicine%202008/AutoDock%20Tutorial.pdf

In [ ]:


from SBLMDCOVDOCK.SBLSettings import DOCKING_Settings
from SBLMDCOVDOCK.md_setuptools import plot_xvg
import pickle
from copy import deepcopy
import subprocess

import pandas as pd
import os
import glob

# import gmxapi as gmx
import subprocess
import matplotlib.pyplot as plt

settings = DOCKING_Settings()
main_dir = os.getcwd()

# AMPC - https://journals.asm.org/doi/10.1128/AAC.02073-20
ampc = "6T3D"
# KPC-2 - BLDB: http://dx.doi.org/10.1021/ACS.JMEDCHEM.7B00158
kpc2 = "5UL8"
# OXA-10 - BLDB: https://www.pnas.org/doi/full/10.1073/pnas.241442898
oxa10 = "1K55"

structures = pd.DataFrame({"PDBID": [ampc, kpc2, oxa10], 
                           "Name": ["AmpC", "KPC2", "OXA10"],
                           "Cat_Ser": [64,70,67]})

settings.trial_name = "non_covalent"

In [ ]:
prepare_ligand_path = os.path.join(settings.structures_input, "prepare_ligand4.py")
print(prepare_ligand_path)
print(os.path.exists(prepare_ligand_path))
print(main_dir)
os.chdir(main_dir)

In [ ]:
ligands = os.listdir(settings.structures_input)
print(settings.structures_input)
ligands = [ligand for ligand in ligands if ligand.endswith(".sdf")]
print(ligands)

In [ ]:
topo_dir  = "/home/alexi/Documents/SBL_MD_CovDock/topology/Dock"


In [ ]:
for pdb in structures.PDBID:
    data_dir = os.path.join(settings.data_directory, settings.parent, pdb)
    os.makedirs(data_dir, exist_ok=True)
    pdb_file = f"APO_{pdb}_chimeraFH.pdb"
    pdb_path = os.path.join(topo_dir, pdb_file)
    # copy from topo dir to data dir 
    subprocess.run(["cp", pdb_path, data_dir])

In [ ]:
pythonsh= "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh"

for pdb in structures.PDBID:
    data_dir = os.path.join(settings.data_directory, settings.parent, pdb)

    script_name = 'prepare_receptor4.py'
    prepare_rec_path = os.path.join(*[".."]*3,
                                    os.path.join(settings.config, settings.parent, script_name))
    pdb_file = f"APO_{pdb}_chimeraFH.pdb"

    out_pdb_name = "APO_" +pdb + "_ADT" + ".pdb"
    pdbqt_name = out_pdb_name.replace(".pdb", ".pdbqt")

    prepare_receptor_command = [pythonsh, prepare_rec_path,
                                "-r", pdb_file,
                                "-o", pdbqt_name,
                                # "-A", "checkhydrogens",
                                "-e", 
                                "-v",

                                ]

    print(" ".join(prepare_receptor_command))
    subprocess.run(prepare_receptor_command, cwd=data_dir, check=True)




In [ ]:
os.getcwd()

In [ ]:
import subprocess
pythonsh= "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh"
# os.chdir(settings.structures_input)

for idx, lig in enumerate(ligands):
    for pdb in structures.PDBID:
      data_dir = os.path.join(*[".."]*2,
                              settings.data_directory, settings.parent, pdb)

      lig_pdb = lig.replace(".sdf", ".pdb")
      print(idx, lig, lig_pdb)
      lig_pdb_path = os.path.join(data_dir, lig_pdb)
      obabel_command = ["obabel", 
                        "-i", "sdf", 
                        "-o", "pdb", lig, 
                        "-O", lig_pdb_path, 
                      #   "-h"
                        ]

      subprocess.run(obabel_command, 
                        check=True,
                        cwd=settings.structures_input)

      # break
  # os.chdir(main_dir)


In [ ]:
data_dir = os.path.join(settings.data_directory, settings.parent, pdb)

os.listdir(data_dir)

In [ ]:
import subprocess
pythonsh= "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh"
# os.chdir(settings.structures_input)
ligs = []
for idx, lig in enumerate(ligands):
    for pdb in structures.PDBID:
        data_dir = os.path.join(settings.data_directory, settings.parent, pdb)

        lig_pdb = lig.replace(".sdf", ".pdb")

        script = "prepare_ligand4.py"

        lig_out = lig_pdb.replace(".pdb", ".pdbqt")

        lig_pdb = os.path.join(data_dir, lig_pdb)
        lig_out = os.path.join(data_dir, lig_out)    

        print(idx, lig_pdb, lig_out)
        script_path = os.path.join(settings.structures_input, script)
        preplig4_command = [pythonsh, script_path, 
                            "-l", lig_pdb, 
                            "-o", lig_out,
                            "-A", "bonds_hydrogens",
                            "-U", "nphs_lps",
                            "-v"]
        try:
            subprocess.run(preplig4_command, 
                        check=True)
            ligs.append(lig.replace(".sdf", ""))
        except:
            pass

        # break
    # os.chdir(main_dir)


In [ ]:
for pdb in structures.PDBID:
    #print number of pdb and pdbqt files
    data_dir = os.path.join(settings.data_directory, settings.parent, pdb)
    print(pdb, len(os.listdir(data_dir)))
    pdbs = [pdb for pdb in os.listdir(data_dir) if pdb.endswith(".pdb")]
    pdbqts = [pdb for pdb in os.listdir(data_dir) if pdb.endswith(".pdbqt")]
    print(pdb, len(pdbs), len(pdbqts))


In [ ]:
pythonsh= "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh"
modified_param_line = "parameter_file "+ os.path.join("..","..","..",settings.config, 
                                                        settings.parent, 
                                                        "AD4.1_bound.dat") + "\n"


for pdb in structures.PDBID:
        data_dir = os.path.join(settings.data_directory, settings.parent, pdb)

        for lig in os.listdir(data_dir):
            if lig.endswith(".pdb"):
                continue
            if "APO" in lig:
                continue
            lig = lig.replace(".pdbqt", "")
            # APO_1K55_ADT
            print(pdb, lig)

            # break
            script_name = "prepare_gpf4.py"
            prepare_grid_path = os.path.join(*[".."]*3,os.path.join(settings.config, settings.parent, script_name))

            pdb_name = "APO_" +pdb + "_ADT" + ".pdb"
            pdbqt_name = pdb_name.replace(".pdb", ".pdbqt")
            pdbqt_path = os.path.join(data_dir, pdbqt_name)
            ligand_name = lig + ".pdbqt"
            ligand_path = os.path.join(data_dir, ligand_name)
            grid_out = lig +"_"+ pdbqt_name.replace(".pdbqt", ".gpf")
            prep_grid_command = [pythonsh,
                                prepare_grid_path,
                                "-r", pdbqt_name,
                                "-l", ligand_name,
                                "-o", grid_out,
                                # "-p", "ligand_types='H,HD,HS,C,A,N,NA,NS,OA,OS,F,Mg,Mn,Zn,Ca,Fe,Cl,Br,I,SA,S,Se,P,GA,GC,GN,GO,GP,G'",
                                
                                "-v"]
            
            
            print(" ".join(prep_grid_command))
            dir = "/home/alexi/Documents/SBL_MD_CovDock/topology/Dock"
            # break
            subprocess.run(prep_grid_command,check=True, cwd=data_dir)
            with open(os.path.join(data_dir, grid_out), "r+") as f:
                lines = f.readlines()

                new_lines = []

                new_lines.append(modified_param_line)
                for line in lines:
                    new_lines.append(line)

                # Write modified lines back to the file
                f.seek(0)
                f.writelines(new_lines)
                f.truncate()     


            # break

    # break

In [ ]:
pythonsh= "/home/alexi/Documents/ADFRsuite_x86_64Linux_1.0/bin/pythonsh"


for pdb in structures.PDBID:
        break
        data_dir = os.path.join(settings.data_directory, settings.parent, pdb)

        for lig in os.listdir(data_dir):
            if lig.endswith(".pdb"):
                continue
            if "APO" in lig:
                continue
            lig = lig.replace(".pdbqt", "")
            script_name = "prepare_dpf4.py"
            prepare_dock_path = os.path.join(*[".."]*3,os.path.join(settings.config, settings.parent, script_name))

            pdb_name = "APO_" +pdb + "_ADT" + ".pdb"
            pdbqt_name = pdb_name.replace(".pdb", ".pdbqt")
            ligand_name = lig + ".pdbqt"
            prep_dock_command = [pythonsh,
                                prepare_dock_path,
                                "-l", ligand_name,
                                "-r", pdbqt_name,
                                "-o", lig +"_"+ pdbqt_name.replace(".pdbqt", ".dpf"),
                                "-v"]

            print(" ".join(prep_dock_command))

            subprocess.run(prep_dock_command, cwd=data_dir, check=True)




In [ ]:
print(os.getcwd())

In [ ]:
print(os.listdir(dir))

In [52]:

autodockgpu_dir = "/home/alexi/Documents/AutoDock-GPU/bin"
engine = "CUDA_64"

autodockgpu = f"autodock_{engine}wi"
auto_dock = os.path.join(autodockgpu_dir, autodockgpu)
docked = []
# for pdb in structures.PDBID:

for pdb in structures.PDBID:
        data_dir = os.path.join(settings.data_directory, settings.parent, pdb)

        for lig in os.listdir(data_dir):
            if lig.endswith(".pdb"):
                continue
            if "APO" in lig:
                continue
            if ".pdbqt" not in lig:
                continue
            print(pdb, lig)
            lig = lig.replace(".pdbqt", "")
            name = "APO_" +pdb + "_ADT"
            pdb_name =  name + ".pdb"
            pdbqt_name = pdb_name.replace(".pdb", ".pdbqt")
            grid_name = lig +"_"+ pdbqt_name.replace(".pdbqt", ".gpf")
            grid_log = grid_name.replace(".gpf", ".glg")

            autogrid_command = ["autogrid4", 
                                "-p", grid_name, 
                                "-l", grid_log, 
                                "-d", f"{lig}_{name}.maps.fld",
                                "-o", f"{lig}_{name}.maps.map",
                                "-v"]

            dock_name = lig +"_"+ pdbqt_name.replace(".pdbqt", ".dpf")
            dock_log = dock_name.replace(".dpf", ".dlg")

            autodock_command = [auto_dock, 
                                # "-p", dock_name, 
                                # "-l", dock_log, 
                                "-M",  f"{name}.maps.fld", 
                                "-L", f"{lig}.pdbqt",
                                "--lsmet", "ad",
                                # "--psize", "50",
                                # "--nrun", "50",
                                "-v"]


            dir = "/home/alexi/Documents/SBL_MD_CovDock/topology/Dock"
            # print(os.listdir(dir))
            # try:
            subprocess.run(autogrid_command, check=True,cwd=data_dir)
            subprocess.run(autodock_command, check=True,cwd=data_dir)
            print("Docking successful")
            docked.append((lig, pdb))
            # except:
            #     pass
            # break
print(docked)

6T3D PCZ.pdbqt



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 63



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 64



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 308



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 309



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 351



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 352



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 480



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 481



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 535



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 535



autogrid4: WARNING:  Found an H-bonding a

AutoDock-GPU version: v1.5.3-53-gf58a5173fa2f4c82a74b40bc895ad7e65de59f47

Running 1 docking calculation

Cuda device:                              NVIDIA GeForce RTX 3060
Available memory on device:               11626 MB (total: 12022 MB)

CUDA Setup time 0.060974s

Running Job #1
    Using heuristics: (capped) number of evaluations set to 2040163
    Local-search chosen method is: ADADELTA (ad)

Rest of Setup time 0.002991s

Executing docking runs, stopping automatically after either reaching 0.15 kcal/mol standard deviation of
the best molecules of the last 4 * 5 generations, 42000 generations, or 2040163 evaluations:

Generations |  Evaluations |     Threshold    |  Average energy of best 10%  | Samples |    Best energy
------------+--------------+------------------+------------------------------+---------+-------------------
          0 |          150 |258418.72 kcal/mol |107722.43 +/-40185.68 kcal/mol |       4 |71748.43 kcal/mol
          5 |        28923 |258418.72 kcal/mol |7


autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 63



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 64



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 308



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 309



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 351



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 352



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 480



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 481



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 535



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 535



autogrid4: WARNING:  Found an H-bonding a

AutoDock-GPU version: v1.5.3-53-gf58a5173fa2f4c82a74b40bc895ad7e65de59f47

Running 1 docking calculation

Cuda device:                              NVIDIA GeForce RTX 3060
Available memory on device:               11626 MB (total: 12022 MB)

CUDA Setup time 0.042112s

Running Job #1
    Using heuristics: (capped) number of evaluations set to 1259779
    Local-search chosen method is: ADADELTA (ad)

Rest of Setup time 0.002816s

Executing docking runs, stopping automatically after either reaching 0.15 kcal/mol standard deviation of
the best molecules of the last 4 * 5 generations, 42000 generations, or 1259779 evaluations:

Generations |  Evaluations |     Threshold    |  Average energy of best 10%  | Samples |    Best energy
------------+--------------+------------------+------------------------------+---------+-------------------
          0 |          150 |97926.14 kcal/mol |39050.12 +/-21419.66 kcal/mol |       4 |14332.95 kcal/mol
          5 |        30808 |119373.84 kcal/mol |234

...

AutoDock-GPU version: v1.5.3-53-gf58a5173fa2f4c82a74b40bc895ad7e65de59f47

Running 1 docking calculation

Cuda device:                              NVIDIA GeForce RTX 3060
Available memory on device:               11626 MB (total: 12022 MB)

CUDA Setup time 0.044064s

Running Job #1
    Using heuristics: (capped) number of evaluations set to 1259779
    Local-search chosen method is: ADADELTA (ad)

Rest of Setup time 0.002839s

Executing docking runs, stopping automatically after either reaching 0.15 kcal/mol standard deviation of
the best molecules of the last 4 * 5 generations, 42000 generations, or 1259779 evaluations:

Generations |  Evaluations |     Threshold    |  Average energy of best 10%  | Samples |    Best energy
------------+--------------+------------------+------------------------------+---------+-------------------
          0 |          150 | 4509.96 kcal/mol | 2022.77 +/-  663.25 kcal/mol |       4 |  907.57 kcal/mol
          5 |        35049 | 4509.96 kcal/mol |  66


autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 744



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 745



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 1244



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 1245




AutoDock-GPU version: v1.5.3-53-gf58a5173fa2f4c82a74b40bc895ad7e65de59f47

Running 1 docking calculation

Cuda device:                              NVIDIA GeForce RTX 3060
Available memory on device:               11626 MB (total: 12022 MB)

CUDA Setup time 0.035512s

Running Job #1
    Using heuristics: (capped) number of evaluations set to 1613968
    Local-search chosen method is: ADADELTA (ad)

Rest of Setup time 0.002869s

Executing docking runs, stopping automatically after either reaching 0.15 kcal/mol standard deviation of
the best molecules of the last 4 * 5 generations, 42000 generations, or 1613968 evaluations:

Generations |  Evaluations |     Threshold    |  Average energy of best 10%  | Samples |    Best energy
------------+--------------+------------------+------------------------------+---------+-------------------
          0 |          150 |51349.59 kcal/mol |19339.76 +/- 8535.96 kcal/mol |       4 | 8602.91 kcal/mol
          5 |        31887 |51349.59 kcal/mol | 708


autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 744



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 745



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 1244



autogrid4: WARNING:  Found an H-bonding atom with three bonded atoms, atom serial number 1245




AutoDock-GPU version: v1.5.3-53-gf58a5173fa2f4c82a74b40bc895ad7e65de59f47

Running 1 docking calculation

Cuda device:                              NVIDIA GeForce RTX 3060
Available memory on device:               11626 MB (total: 12022 MB)

CUDA Setup time 0.041662s

Running Job #1
    Using heuristics: (capped) number of evaluations set to 1613968
    Local-search chosen method is: ADADELTA (ad)

Rest of Setup time 0.003033s

Executing docking runs, stopping automatically after either reaching 0.15 kcal/mol standard deviation of
the best molecules of the last 4 * 5 generations, 42000 generations, or 1613968 evaluations:

Generations |  Evaluations |     Threshold    |  Average energy of best 10%  | Samples |    Best energy
------------+--------------+------------------+------------------------------+---------+-------------------
          0 |          150 |26351.06 kcal/mol |11057.31 +/- 4244.72 kcal/mol |       4 | 4172.49 kcal/mol
          5 |        33009 |26975.02 kcal/mol | 324

In [ ]:
print(docked)